# Propeller
* Run the scene workshop1.ttt in CoppeliaSim

In [161]:
import sim
%pylab inline

Populating the interactive namespace from numpy and matplotlib


### Check if python is connecting to Coppelia

In [162]:
sim.simxFinish(-1)  # Close opened connections
clientID = sim.simxStart('127.0.0.1', 19999, True, True, 5000, 5)  # Connect to CoppeliaSim

if clientID != -1:
    print('Connected')

    # Now try to retrieve data in a blocking fashion (i.e. a service call):
    res, objs = sim.simxGetObjects(clientID, sim.sim_handle_all, sim.simx_opmode_blocking)

    print('Simulation time in milliseconds: ', sim.simxGetLastCmdTime(clientID))
    
    # Get Object position
    name = 'propeller'
    err_code, cuboid = sim.simxGetObjectHandle(clientID, name, sim.simx_opmode_blocking)
    res, position = sim.simxGetObjectPosition(clientID, cuboid, -1, sim.simx_opmode_blocking)        
#     print(name, 'is at [x,y,z]=', position)
    
    
    returnCode = sim.simxSetFloatSignal(clientID,'f', 100.0,sim.simx_opmode_oneshot)
#     returnCode, signalValue=sim.simxGetFloatSignal(clientID,'particleVelocity',sim.simx_opmode_oneshot_wait)
#     print(signalValue)
    
    # Now close the connection to CoppeliaSim:
    sim.simxGetPingTime(clientID)
    sim.simxFinish(clientID)
    print('Disconnected')
else:
    print('Failed connecting to remote API server')


Connected
Simulation time in milliseconds:  87850
Disconnected


# Robot

In [163]:
class robot():
    
    def __init__(self, frame_name, motor_names=[], client_id=0):  
        # If there is an existing connection
        if client_id:
                self.client_id = client_id
        else:
            self.client_id = self.open_connection()
            
        self.motors = self._get_handlers(motor_names) 
        
        # Robot frame
        self.frame =  self._get_handler(frame_name)
            
        
    def open_connection(self):
        sim.simxFinish(-1)  # just in case, close all opened connections
        self.client_id = sim.simxStart('127.0.0.1', 19999, True, True, 5000, 5)  # Connect to CoppeliaSim 
        
        if clientID != -1:
            print('Robot connected')
        else:
            print('Connection failed')
        return clientID
        
    def close_connection(self):    
        sim.simxGetPingTime(self.client_id)  # Before closing the connection to CoppeliaSim, make sure that the last command sent out had time to arrive.
        sim.simxFinish(self.client_id)  # Now close the connection to CoppeliaSim:
        print('Connection closed')
    
    def isConnected(self):
        c,result = sim.simxGetPingTime(self.client_id)
        # Return true if the robot is connected
        return result > 0         
        
    def _get_handler(self, name):
        err_code, handler = sim.simxGetObjectHandle(self.client_id, name, sim.simx_opmode_blocking)
        return handler
    
    def _get_handlers(self, names):
        handlers = []
        for name in names:
            handler = self._get_handler(name)
            handlers.append(handler)
        
        return handlers

    def send_motor_velocities(self, vels):
        for motor, vel in zip(self.motors, vels):
            err_code = sim.simxSetJointTargetVelocity(self.client_id, 
                                                      motor, vel, sim.simx_opmode_streaming)      
            
    def set_position(self, position, relative_object=-1):
        if relative_object != -1:
            relative_object = self._get_handler(relative_object)        
        sim.simxSetObjectPosition(clientID, self.frame, relative_object, position, sim.simx_opmode_oneshot)
        
    def simtime(self):
        return sim.simxGetLastCmdTime(self.client_id)
    
    def get_position(self, relative_object=-1):
        # Get position relative to an object, -1 for global frame
        if relative_object != -1:
            relative_object = self._get_handler(relative_object)
        res, position = sim.simxGetObjectPosition(self.client_id, self.frame, relative_object, sim.simx_opmode_oneshot)        
        return array(position)
    
    def get_velocity(self, relative_object=-1):
        # Get velocity relative to an object, -1 for global frame
        if relative_object != -1:
            relative_object = self._get_handler(relative_object)
        res, velocity, omega = sim.simxGetObjectVelocity(self.client_id, self.frame, sim.simx_opmode_oneshot)        
        return array(velocity), array(omega)
    
    def get_object_position(self, object_name):
        # Get Object position in the world frame
        err_code, object_h = sim.simxGetObjectHandle(self.client_id, object_name, sim.simx_opmode_oneshot)
        res, position = sim.simxGetObjectPosition(self.client_id, object_h, -1, sim.simx_opmode_oneshot)
        return array(position)
    
    def get_object_relative_position(self, object_name):        
        # Get Object position in the robot frame
        err_code, object_h = sim.simxGetObjectHandle(self.client_id, object_name, sim.simx_opmode_oneshot)
        res, position = sim.simxGetObjectPosition(self.client_id, object_h, self.frame, sim.simx_opmode_oneshot)
        return array(position)
    
    def set_force(self, f, signal='f'):
        return sim.simxSetFloatSignal(clientID, signal, f, sim.simx_opmode_oneshot)
    
    def set_forces(self, f, signal='f'):
        # For many propellers
        for i, fi in enumerate(f):
            signali = signal + str(i+1)
            sim.simxSetFloatSignal(clientID, signali, fi, sim.simx_opmode_oneshot)
    
       # Added this, Was missing get orientation
    def get_orientation(self, relative_object=-1): 
        # Retrieves the orientation (Euler angles) of an object.
        if relative_object != -1:
            relative_object = self._get_handler(relative_object)
        res, orientation = sim.simxGetObjectOrientation(self.client_id, self.frame, relative_object, sim.simx_opmode_oneshot)        
        return array(orientation)
    
        

In [164]:
# Send force to a robot
r = robot('Cuboid')  # Create an instance of our robot
r.set_force(100)

r.close_connection()  

Robot connected
Connection closed


# P-Control

In [165]:

# Rotation matrices
RotX = lambda ϕ: [[1, 0, 0], 
         [0, cos(ϕ), -sin(ϕ)],
         [0, sin(ϕ), cos(ϕ)]]
RotY = lambda θ: [[cos(θ), 0, sin(θ)], 
         [0, 1, 0],
         [-sin(θ), 0, cos(θ)]]
RotZ = lambda ψ: [[cos(ψ), -sin(ψ), 0], 
        [sin(ψ), cos(ψ), 0],
        [0, 0, 1]]
RotZYX = lambda Θ: np.dot(RotZ(Θ[2]), np.dot(RotY(Θ[1]), RotX(Θ[0])))


# Rotation Euler Angles Tait-Bryan convention - https://coppeliarobotics.com/helpFiles/en/eulerAngles.htm
import numpy as np

# Rotation around Z-axis 
def yaw_rotateX(w):
    yaw = np.array([[1, 0, 0], [0 , np.cos(w),  - np.sin(w)], [0, np.sin(w), np.cos(w)]])  
    return yaw


# Rotation around Y-axis 
def pitch_rotateY(v):
    pitch = np.array([[np.cos(v), 0 , np.sin(v)], [0, 1, 0], [-np.sin(v), 0, np.cos(v)]])   
    return pitch


# Rotation around z-axis 
def roll_rotateZ(u):
    roll = np.array([ [np.cos(u), - np.sin(u), 0], [np.sin(u), np.cos(u), 0], [0, 0, 1]])  
    return roll


In [166]:
# Propeller orientations
angles = [(0, pi/4), (0, -pi/4), (0, -pi/4), (0, pi/4), 
         (3*pi/4, 0), (3*pi/4, 0), (-3*pi/4, 0), (-3*pi/4, 0)]
R_prop = [RotZYX((ϕ, θ, 0)) for ϕ, θ in angles]
e3 = array([[0],[0],[1]])
z_prop = [np.dot(Ri, e3) for Ri in R_prop]
# Propeller locations
p = [(1, -1, 1), (-1, -1, 1), (-1, 1, 1), (1, 1, 1),
    (1, -1, -1), (-1, -1, -1), (-1, 1, -1), (1, 1, -1)]
# scale locations
d = 0.1  # distance of the arm in an axis
p = d * array(p)
# A matrix
A_force = np.hstack(z_prop)
A_torque = np.hstack([np.cross(pi, zi.T).T for pi, zi in zip(p, z_prop)])
A = np.vstack((A_force, A_torque))
print(A)
Apinv = np.linalg.pinv(A)

[[ 7.07106781e-01 -7.07106781e-01 -7.07106781e-01  7.07106781e-01
   0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
  -7.07106781e-01 -7.07106781e-01  7.07106781e-01  7.07106781e-01]
 [ 7.07106781e-01  7.07106781e-01  7.07106781e-01  7.07106781e-01
  -7.07106781e-01 -7.07106781e-01 -7.07106781e-01 -7.07106781e-01]
 [-7.07106781e-02 -7.07106781e-02  7.07106781e-02  7.07106781e-02
  -1.38777878e-17 -1.38777878e-17  1.38777878e-17  1.38777878e-17]
 [ 0.00000000e+00  0.00000000e+00  0.00000000e+00  0.00000000e+00
   7.07106781e-02 -7.07106781e-02 -7.07106781e-02  7.07106781e-02]
 [ 7.07106781e-02 -7.07106781e-02  7.07106781e-02 -7.07106781e-02
  -7.07106781e-02  7.07106781e-02 -7.07106781e-02  7.07106781e-02]]


In [167]:
# omega = (math.abs(propForce)^0.5) / kf  * (propForce/math.abs(propForce))
# what was the above code for ?

In [ ]:

m = 8 + 0.1 #kg mass of the block plus the mass of the prop
g = 9.8
I = 80

log = []

import math
# Send force to a robot
r = robot('Cuboid')  # Create an instance of our robot

# propellers .1 each
m = 8.8 #kg mass of the block plus the mass of the prop
g = 9.81
I = 80


log = []
print("r position:", r.get_position())
# print("d position:", d.get_position())

print("r orientation:", r.get_orientation())
wrench = [0, 0, 0, 0, 0, 0]
r.set_forces(wrench)

try:

    while True:
        # Robot state
        p = r.get_position()
        v, ω = r.get_velocity()
        theta = r.get_orientation()

        # Desired state
        p_d = [0, 0, 2] # Because we want it to be flying, in the air 
        v_d, ω_d = 0,0
        theta_d = [0, 0, 0]
        # theta_d = [0, 0, np.pi/6]


        ep = p_d - p
        print("---ep: ", ep)
        ev = v_d - v
        eω = ω_d - ω
        # error in orientation
        et = theta_d - theta 


        kp, kd = .1, 1 
        a = kp * ep + kd * ev
        

        # angular acceleration
        kp_th , kd_th = 0.0004, 0.002 
        ath = kp_th * et + kd_th * eω 
        torq = I * ath 


        f = m * a
        f[2] += m*g

       # To world frame
       # https://help.naturalpoint.com/kb/articles/transform-world-space-coordinates-to-local-rigid-body-coordinates
       # R =  yaw_rotateX( theta_d[0])  * pitch_rotateY(theta_d[1]) * roll_rotateZ( theta_d[2] )

        R = RotZYX(theta_d)
        f_d = np.dot(R, f) 
        # print("u:", u)
        
        wrench = [f_d[0], f_d[1], f_d[2], torq[0], torq[1], torq[2]]
        u = np.dot(Apinv, wrench)
        r.set_forces(u.tolist())
        
        # r.wrench( [f_d[0], f_d[1], f_d[2], torq[0], torq[1], torq[2]])
        
        log.append(ep)
        time.sleep(0.001)
except KeyboardInterrupt:
    r.close_connection()
    

r.close_connection()  

Robot connected
r position: [0. 0. 0.]
r orientation: [0. 0. 0.]
---ep:  [0. 0. 2.]
---ep:  [0. 0. 2.]
---ep:  [0. 0. 2.]
---ep:  [0. 0. 2.]
---ep:  [-1.66467857e-03  3.76464683e-03  1.82859071e+00]
---ep:  [-1.66467857e-03  3.76464683e-03  1.82859071e+00]
---ep:  [-1.66467857e-03  3.76464683e-03  1.82859071e+00]
---ep:  [-1.66467857e-03  3.76464683e-03  1.82859071e+00]
---ep:  [-1.66467857e-03  3.76464683e-03  1.82859071e+00]
---ep:  [-1.67903141e-03  3.63091053e-03  1.82803248e+00]
---ep:  [-1.67903141e-03  3.63091053e-03  1.82803248e+00]
---ep:  [-1.69019564e-03  3.50421411e-03  1.82700016e+00]
---ep:  [-1.69019564e-03  3.50421411e-03  1.82700016e+00]
---ep:  [-1.69519172e-03  3.38143995e-03  1.82551099e+00]
---ep:  [-1.69519172e-03  3.38143995e-03  1.82551099e+00]
---ep:  [-1.69519172e-03  3.38143995e-03  1.82551099e+00]
---ep:  [-1.69519172e-03  3.38143995e-03  1.82551099e+00]
---ep:  [-1.69519172e-03  3.38143995e-03  1.82551099e+00]
---ep:  [-1.69244804e-03  3.26241250e-03  1.823

---ep:  [ 0.00756817 -0.02158638  1.35229439]
---ep:  [ 0.00756817 -0.02158638  1.35229439]
---ep:  [ 0.00756817 -0.02158638  1.35229439]
---ep:  [ 0.00756817 -0.02158638  1.35229439]
---ep:  [ 0.00756817 -0.02158638  1.35229439]
---ep:  [ 0.00765895 -0.02194339  1.34495217]
---ep:  [ 0.00765895 -0.02194339  1.34495217]
---ep:  [ 0.00774751 -0.02229163  1.33764005]
---ep:  [ 0.00774751 -0.02229163  1.33764005]
---ep:  [ 0.00783388 -0.02263092  1.33035845]
---ep:  [ 0.00783388 -0.02263092  1.33035845]
---ep:  [ 0.00783388 -0.02263092  1.33035845]
---ep:  [ 0.00791804 -0.02296101  1.3231076 ]
---ep:  [ 0.00791804 -0.02296101  1.3231076 ]
---ep:  [ 0.00800003 -0.02328181  1.31588775]
---ep:  [ 0.00800003 -0.02328181  1.31588775]
---ep:  [ 0.00807988 -0.02359323  1.30869925]
---ep:  [ 0.00807988 -0.02359323  1.30869925]
---ep:  [ 0.00807988 -0.02359323  1.30869925]
---ep:  [ 0.00807988 -0.02359323  1.30869925]
---ep:  [ 0.00807988 -0.02359323  1.30869925]
---ep:  [ 0.00815761 -0.02389522  

---ep:  [ 0.00958358 -0.02689494  0.87638831]
---ep:  [ 0.00955513 -0.02680309  0.87149394]
---ep:  [ 0.00955513 -0.02680309  0.87149394]
---ep:  [ 0.00952548 -0.0267107   0.8666265 ]
---ep:  [ 0.00952548 -0.0267107   0.8666265 ]
---ep:  [ 0.00949461 -0.02661785  0.86178613]
---ep:  [ 0.00949461 -0.02661785  0.86178613]
---ep:  [ 0.00946251 -0.02652458  0.85697281]
---ep:  [ 0.00946251 -0.02652458  0.85697281]
---ep:  [ 0.00942917 -0.02643097  0.85218608]
---ep:  [ 0.00942917 -0.02643097  0.85218608]
---ep:  [ 0.00942917 -0.02643097  0.85218608]
---ep:  [ 0.00942917 -0.02643097  0.85218608]
---ep:  [ 0.00939461 -0.02633707  0.84742618]
---ep:  [ 0.00939461 -0.02633707  0.84742618]
---ep:  [ 0.00935888 -0.02624298  0.84269261]
---ep:  [ 0.00935888 -0.02624298  0.84269261]
---ep:  [ 0.00935888 -0.02624298  0.84269261]
---ep:  [ 0.00935888 -0.02624298  0.84269261]
---ep:  [ 0.00935888 -0.02624298  0.84269261]
---ep:  [ 0.009322   -0.02614875  0.83798528]
---ep:  [ 0.009322   -0.02614875  

---ep:  [ 0.00412627 -0.02066036  0.55043721]
---ep:  [ 0.00412627 -0.02066036  0.55043721]
---ep:  [ 0.00412627 -0.02066036  0.55043721]
---ep:  [ 0.00403303 -0.02061148  0.54736114]
---ep:  [ 0.00403303 -0.02061148  0.54736114]
---ep:  [ 0.00403303 -0.02061148  0.54736114]
---ep:  [ 0.00393935 -0.02056308  0.54430223]
---ep:  [ 0.00384525 -0.02051516  0.54126036]
---ep:  [ 0.00384525 -0.02051516  0.54126036]
---ep:  [ 0.00384525 -0.02051516  0.54126036]
---ep:  [ 0.00384525 -0.02051516  0.54126036]
---ep:  [ 0.00384525 -0.02051516  0.54126036]
---ep:  [ 0.00375072 -0.0204677   0.53823543]
---ep:  [ 0.00375072 -0.0204677   0.53823543]
---ep:  [ 0.0036558  -0.02042069  0.53522754]
---ep:  [ 0.0036558  -0.02042069  0.53522754]
---ep:  [ 0.00356051 -0.02037413  0.53223634]
---ep:  [ 0.00356051 -0.02037413  0.53223634]
---ep:  [ 0.00346485 -0.02032801  0.52926183]
---ep:  [ 0.00346485 -0.02032801  0.52926183]
---ep:  [ 0.00336883 -0.02028232  0.52630401]
---ep:  [ 0.00336883 -0.02028232  

---ep:  [-0.00418053 -0.017527    0.34763563]
---ep:  [-0.00418053 -0.017527    0.34763563]
---ep:  [-0.00428392 -0.01749426  0.34569287]
---ep:  [-0.00428392 -0.01749426  0.34569287]
---ep:  [-0.00428392 -0.01749426  0.34569287]
---ep:  [-0.00428392 -0.01749426  0.34569287]
---ep:  [-0.00438725 -0.01746175  0.34376109]
---ep:  [-0.00438725 -0.01746175  0.34376109]
---ep:  [-0.00438725 -0.01746175  0.34376109]
---ep:  [-0.00449051 -0.01742948  0.34183979]
---ep:  [-0.00449051 -0.01742948  0.34183979]
---ep:  [-0.0045937  -0.01739745  0.33992934]
---ep:  [-0.0045937  -0.01739745  0.33992934]
---ep:  [-0.00469682 -0.01736566  0.3380295 ]
---ep:  [-0.00469682 -0.01736566  0.3380295 ]
---ep:  [-0.00469682 -0.01736566  0.3380295 ]
---ep:  [-0.00469682 -0.01736566  0.3380295 ]
---ep:  [-0.00469682 -0.01736566  0.3380295 ]
---ep:  [-0.00479986 -0.01733412  0.33614028]
---ep:  [-0.00479986 -0.01733412  0.33614028]
---ep:  [-0.00490279 -0.01730282  0.33426166]
---ep:  [-0.00490279 -0.01730282  

...

---ep:  [-3.25854346e-02 -1.17636751e-02 -7.15255737e-06]
---ep:  [-3.27258036e-02 -1.17661646e-02 -7.15255737e-06]
---ep:  [-3.28661725e-02 -1.17686307e-02 -7.15255737e-06]
---ep:  [-3.28661725e-02 -1.17686307e-02 -7.15255737e-06]
---ep:  [-3.28661725e-02 -1.17686307e-02 -7.15255737e-06]
---ep:  [-3.28661725e-02 -1.17686307e-02 -7.15255737e-06]
---ep:  [-3.28661725e-02 -1.17686307e-02 -7.15255737e-06]
---ep:  [-3.30065414e-02 -1.17710419e-02 -7.15255737e-06]
---ep:  [-3.30065414e-02 -1.17710419e-02 -7.15255737e-06]
---ep:  [-3.31468806e-02 -1.17733637e-02 -7.15255737e-06]
---ep:  [-3.31468806e-02 -1.17733637e-02 -7.15255737e-06]
---ep:  [-3.32871899e-02 -1.17755542e-02 -7.15255737e-06]
---ep:  [-3.32871899e-02 -1.17755542e-02 -7.15255737e-06]
---ep:  [-3.32871899e-02 -1.17755542e-02 -7.15255737e-06]
---ep:  [-3.32871899e-02 -1.17755542e-02 -7.15255737e-06]
---ep:  [-3.34274992e-02 -1.17775695e-02 -7.15255737e-06]
---ep:  [-3.34274992e-02 -1.17775695e-02 -7.15255737e-06]
---ep:  [-3.34

---ep:  [-4.22573946e-02 -1.17446063e-02 -7.15255737e-06]
---ep:  [-4.22573946e-02 -1.17446063e-02 -7.15255737e-06]
---ep:  [-4.22573946e-02 -1.17446063e-02 -7.15255737e-06]
---ep:  [-4.22573946e-02 -1.17446063e-02 -7.15255737e-06]
---ep:  [-4.22573946e-02 -1.17446063e-02 -7.15255737e-06]
---ep:  [-4.23856899e-02 -1.17431376e-02 -7.15255737e-06]
---ep:  [-4.23856899e-02 -1.17431376e-02 -7.15255737e-06]
---ep:  [-4.25136574e-02 -1.17416624e-02 -7.15255737e-06]
---ep:  [-4.25136574e-02 -1.17416624e-02 -7.15255737e-06]
---ep:  [-4.26412895e-02 -1.17401909e-02 -7.15255737e-06]
---ep:  [-4.26412895e-02 -1.17401909e-02 -7.15255737e-06]
---ep:  [-4.27685902e-02 -1.17387436e-02 -7.15255737e-06]
---ep:  [-4.27685902e-02 -1.17387436e-02 -7.15255737e-06]
---ep:  [-4.27685902e-02 -1.17387436e-02 -7.15255737e-06]
---ep:  [-4.28955480e-02 -1.17373336e-02 -7.15255737e-06]
---ep:  [-4.28955480e-02 -1.17373336e-02 -7.15255737e-06]
---ep:  [-4.28955480e-02 -1.17373336e-02 -7.15255737e-06]
---ep:  [-4.28

---ep:  [-4.84977886e-02 -1.17173549e-02 -7.15255737e-06]
---ep:  [-4.84977886e-02 -1.17173549e-02 -7.15255737e-06]
---ep:  [-4.84977886e-02 -1.17173549e-02 -7.15255737e-06]
---ep:  [-4.84977886e-02 -1.17173549e-02 -7.15255737e-06]
---ep:  [-4.84977886e-02 -1.17173549e-02 -7.15255737e-06]
---ep:  [-4.86112274e-02 -1.17187873e-02 -7.15255737e-06]
---ep:  [-4.86112274e-02 -1.17187873e-02 -7.15255737e-06]
---ep:  [-4.86112274e-02 -1.17187873e-02 -7.15255737e-06]
---ep:  [-4.87245210e-02 -1.17202252e-02 -7.15255737e-06]
---ep:  [-4.87245210e-02 -1.17202252e-02 -7.15255737e-06]
---ep:  [-4.87245210e-02 -1.17202252e-02 -7.15255737e-06]
---ep:  [-4.87245210e-02 -1.17202252e-02 -7.15255737e-06]
---ep:  [-4.87245210e-02 -1.17202252e-02 -7.15255737e-06]
---ep:  [-4.88376804e-02 -1.17216343e-02 -7.15255737e-06]
---ep:  [-4.88376804e-02 -1.17216343e-02 -7.15255737e-06]
---ep:  [-4.89507094e-02 -1.17229866e-02 -7.15255737e-06]
---ep:  [-4.89507094e-02 -1.17229866e-02 -7.15255737e-06]
---ep:  [-4.89

---ep:  [-5.66511862e-02 -1.20250415e-02 -7.15255737e-06]
---ep:  [-5.66511862e-02 -1.20250415e-02 -7.15255737e-06]
---ep:  [-5.66511862e-02 -1.20250415e-02 -7.15255737e-06]
---ep:  [-5.66511862e-02 -1.20250415e-02 -7.15255737e-06]
---ep:  [-5.67319877e-02 -1.20335538e-02 -7.15255737e-06]
---ep:  [-5.67319877e-02 -1.20335538e-02 -7.15255737e-06]
---ep:  [-5.68111539e-02 -1.20421536e-02 -7.15255737e-06]
---ep:  [-5.68111539e-02 -1.20421536e-02 -7.15255737e-06]
---ep:  [-5.68111539e-02 -1.20421536e-02 -7.15255737e-06]
---ep:  [-5.68886511e-02 -1.20508391e-02 -7.15255737e-06]
---ep:  [-5.68886511e-02 -1.20508391e-02 -7.15255737e-06]
---ep:  [-5.68886511e-02 -1.20508391e-02 -7.15255737e-06]
---ep:  [-5.69644198e-02 -1.20596113e-02 -7.15255737e-06]
---ep:  [-5.69644198e-02 -1.20596113e-02 -7.15255737e-06]
---ep:  [-5.70384189e-02 -1.20684681e-02 -7.15255737e-06]
---ep:  [-5.70384189e-02 -1.20684681e-02 -7.15255737e-06]
---ep:  [-5.70384189e-02 -1.20684681e-02 -7.15255737e-06]
---ep:  [-5.70

---ep:  [-5.83720133e-02 -1.25349332e-02 -7.15255737e-06]
---ep:  [-5.83536550e-02 -1.25437230e-02 -7.15255737e-06]
---ep:  [-5.83536550e-02 -1.25437230e-02 -7.15255737e-06]
---ep:  [-5.83337769e-02 -1.25521570e-02 -7.15255737e-06]
---ep:  [-5.83337769e-02 -1.25521570e-02 -7.15255737e-06]
---ep:  [-5.83123937e-02 -1.25601916e-02 -7.15255737e-06]
---ep:  [-5.83123937e-02 -1.25601916e-02 -7.15255737e-06]
---ep:  [-5.82894757e-02 -1.25677856e-02 -7.15255737e-06]
---ep:  [-5.82650490e-02 -1.25749130e-02 -7.15255737e-06]
---ep:  [-5.82650490e-02 -1.25749130e-02 -7.15255737e-06]
---ep:  [-5.82391210e-02 -1.25815319e-02 -7.15255737e-06]
---ep:  [-5.82391210e-02 -1.25815319e-02 -7.15255737e-06]
---ep:  [-5.82391210e-02 -1.25815319e-02 -7.15255737e-06]
---ep:  [-5.82391210e-02 -1.25815319e-02 -7.15255737e-06]
---ep:  [-5.82391210e-02 -1.25815319e-02 -7.15255737e-06]
---ep:  [-5.82117252e-02 -1.25876050e-02 -7.15255737e-06]
---ep:  [-5.82117252e-02 -1.25876050e-02 -7.15255737e-06]
---ep:  [-5.81

In [ ]:
plot(log)